**VAE on Maldeb Dataset only**

In [ ]:
import os
import numpy as np
import tensorflow as tf
from keras import layers, Model
import matplotlib.pyplot as plt
import plotly.express as px
from tensorflow.keras.preprocessing.image import img_to_array, load_img

# Sampling layer
class Sampling(layers.Layer):
    """Uses (mean, log_var) to sample z, the vector encoding a digit."""
    def call(self, inputs):
        mean, log_var = inputs
        batch = tf.shape(mean)[0]
        dim = tf.shape(mean)[1]
        epsilon = tf.random.normal(shape=(batch, dim))
        return mean + tf.exp(0.5 * log_var) * epsilon

latent_dim = 3

# Encoder
encoder_inputs = tf.keras.Input(shape=(28, 28, 1))
x = layers.Conv2D(64, 3, activation="relu", strides=2, padding="same")(encoder_inputs)
x = layers.Conv2D(128, 3, activation="relu", strides=2, padding="same")(x)
x = layers.Flatten()(x)
x = layers.Dense(16, activation="relu")(x)
mean = layers.Dense(latent_dim, name="mean")(x)
log_var = layers.Dense(latent_dim, name="log_var")(x)
z = Sampling()([mean, log_var])
encoder = Model(encoder_inputs, [mean, log_var, z], name="encoder")
encoder.summary()

# Decoder
latent_inputs = tf.keras.Input(shape=(latent_dim,))
x = layers.Dense(7 * 7 * 64, activation="relu")(latent_inputs)
x = layers.Reshape((7, 7, 64))(x)
x = layers.Conv2DTranspose(128, 3, activation="relu", strides=2, padding="same")(x)
x = layers.Conv2DTranspose(64, 3, activation="relu", strides=2, padding="same")(x)
decoder_outputs = layers.Conv2DTranspose(1, 3, activation="sigmoid", padding="same")(x)
decoder = Model(latent_inputs, decoder_outputs, name="decoder")
decoder.summary()

# VAE model
class VAE(Model):
    def __init__(self, encoder, decoder, **kwargs):
        super().__init__(**kwargs)
        self.encoder = encoder
        self.decoder = decoder
        self.total_loss_tracker = tf.keras.metrics.Mean(name="total_loss")
        self.reconstruction_loss_tracker = tf.keras.metrics.Mean(name="reconstruction_loss")
        self.kl_loss_tracker = tf.keras.metrics.Mean(name="kl_loss")

    @property
    def metrics(self):
        return [
            self.total_loss_tracker,
            self.reconstruction_loss_tracker,
            self.kl_loss_tracker,
        ]

    def train_step(self, data):
        with tf.GradientTape() as tape:
            mean, log_var, z = self.encoder(data)
            reconstruction = self.decoder(z)
            reconstruction_loss = tf.reduce_mean(
                tf.reduce_sum(
                    tf.keras.losses.binary_crossentropy(data, reconstruction),
                    axis=(1, 2),
                )
            )
            kl_loss = -0.5 * (1 + log_var - tf.square(mean) - tf.exp(log_var))
            kl_loss = tf.reduce_mean(tf.reduce_sum(kl_loss, axis=1))
            total_loss = reconstruction_loss + kl_loss
        grads = tape.gradient(total_loss, self.trainable_weights)
        self.optimizer.apply_gradients(zip(grads, self.trainable_weights))
        self.total_loss_tracker.update_state(total_loss)
        self.reconstruction_loss_tracker.update_state(reconstruction_loss)
        self.kl_loss_tracker.update_state(kl_loss)
        return {
            "loss": self.total_loss_tracker.result(),
            "reconstruction_loss": self.reconstruction_loss_tracker.result(),
            "kl_loss": self.kl_loss_tracker.result(),
        }

# Load Kaggle dataset
def load_images_from_folder(folder):
    images = []
    for filename in os.listdir(folder):
        img = load_img(os.path.join(folder, filename), color_mode='grayscale', target_size=(28, 28))
        if img is not None:
            img_array = img_to_array(img)
            images.append(img_array)
    return np.array(images)

benign_images = load_images_from_folder('/content/drive/MyDrive/debinew/Benign')
malicious_images = load_images_from_folder('/content/drive/MyDrive/debinew/Malicious')

benign_labels = np.zeros(len(benign_images))
malicious_labels = np.ones(len(malicious_images))

images = np.concatenate((benign_images, malicious_images), axis=0)
labels = np.concatenate((benign_labels, malicious_labels), axis=0)

images = images.astype('float32') / 255

# Train VAE
vae = VAE(encoder, decoder)
vae.compile(optimizer=tf.keras.optimizers.Adam())
vae.fit(images, epochs=10, batch_size=128)

# 3D Plotting function with plotly
def plot_latent_space_3d(encoder, data, labels):
    z_mean, _, _ = encoder.predict(data)
    fig = px.scatter_3d(
        x=z_mean[:, 0],
        y=z_mean[:, 1],
        z=z_mean[:, 2],
        color=labels,
        labels={'x': 'z[0]', 'y': 'z[1]', 'z': 'z[2]', 'color': 'Class'},
        title="3D Latent Space"
    )
    fig.show()

# Plot the 3D latent space
plot_latent_space_3d(encoder, images, labels)

Model: "encoder"
__________________________________________________________________________________________________
 Layer (type)                Output Shape                 Param #   Connected to                  
 input_1 (InputLayer)        [(None, 28, 28, 1)]          0         []                            
                                                                                                  
 conv2d (Conv2D)             (None, 14, 14, 64)           640       ['input_1[0][0]']             
                                                                                                  
 conv2d_1 (Conv2D)           (None, 7, 7, 128)            73856     ['conv2d[0][0]']              
                                                                                                  
 flatten (Flatten)           (None, 6272)                 0         ['conv2d_1[0][0]']            
                                                                                            

**VAE on Maldeb Dataset and CIFAR10**

In [ ]:
import os
import numpy as np
import tensorflow as tf
from keras import layers, Model
import matplotlib.pyplot as plt
import plotly.express as px
from tensorflow.keras.preprocessing.image import img_to_array, load_img
from tensorflow.keras.datasets import cifar10

# Sampling layer
class Sampling(layers.Layer):
    """Uses (mean, log_var) to sample z, the vector encoding a digit."""
    def call(self, inputs):
        mean, log_var = inputs
        batch = tf.shape(mean)[0]
        dim = tf.shape(mean)[1]
        epsilon = tf.random.normal(shape=(batch, dim))
        return mean + tf.exp(0.5 * log_var) * epsilon

latent_dim = 3

# Encoder
encoder_inputs = tf.keras.Input(shape=(28, 28, 1))
x = layers.Conv2D(64, 3, activation="relu", strides=2, padding="same")(encoder_inputs)
x = layers.Conv2D(128, 3, activation="relu", strides=2, padding="same")(x)
x = layers.Flatten()(x)
x = layers.Dense(16, activation="relu")(x)
mean = layers.Dense(latent_dim, name="mean")(x)
log_var = layers.Dense(latent_dim, name="log_var")(x)
z = Sampling()([mean, log_var])
encoder = Model(encoder_inputs, [mean, log_var, z], name="encoder")
encoder.summary()

# Decoder
latent_inputs = tf.keras.Input(shape=(latent_dim,))
x = layers.Dense(7 * 7 * 64, activation="relu")(latent_inputs)
x = layers.Reshape((7, 7, 64))(x)
x = layers.Conv2DTranspose(128, 3, activation="relu", strides=2, padding="same")(x)
x = layers.Conv2DTranspose(64, 3, activation="relu", strides=2, padding="same")(x)
decoder_outputs = layers.Conv2DTranspose(1, 3, activation="sigmoid", padding="same")(x)
decoder = Model(latent_inputs, decoder_outputs, name="decoder")
decoder.summary()

# VAE model
class VAE(Model):
    def __init__(self, encoder, decoder, **kwargs):
        super().__init__(**kwargs)
        self.encoder = encoder
        self.decoder = decoder
        self.total_loss_tracker = tf.keras.metrics.Mean(name="total_loss")
        self.reconstruction_loss_tracker = tf.keras.metrics.Mean(name="reconstruction_loss")
        self.kl_loss_tracker = tf.keras.metrics.Mean(name="kl_loss")

    @property
    def metrics(self):
        return [
            self.total_loss_tracker,
            self.reconstruction_loss_tracker,
            self.kl_loss_tracker,
        ]

    def train_step(self, data):
        with tf.GradientTape() as tape:
            mean, log_var, z = self.encoder(data)
            reconstruction = self.decoder(z)
            reconstruction_loss = tf.reduce_mean(
                tf.reduce_sum(
                    tf.keras.losses.binary_crossentropy(data, reconstruction),
                    axis=(1, 2),
                )
            )
            kl_loss = -0.5 * (1 + log_var - tf.square(mean) - tf.exp(log_var))
            kl_loss = tf.reduce_mean(tf.reduce_sum(kl_loss, axis=1))
            total_loss = reconstruction_loss + kl_loss
        grads = tape.gradient(total_loss, self.trainable_weights)
        self.optimizer.apply_gradients(zip(grads, self.trainable_weights))
        self.total_loss_tracker.update_state(total_loss)
        self.reconstruction_loss_tracker.update_state(reconstruction_loss)
        self.kl_loss_tracker.update_state(kl_loss)
        return {
            "loss": self.total_loss_tracker.result(),
            "reconstruction_loss": self.reconstruction_loss_tracker.result(),
            "kl_loss": self.kl_loss_tracker.result(),
        }

# Load Kaggle dataset
def load_images_from_folder(folder):
    images = []
    for filename in os.listdir(folder):
        img = load_img(os.path.join(folder, filename), color_mode='grayscale', target_size=(28, 28))
        if img is not None:
            img_array = img_to_array(img)
            images.append(img_array)
    return np.array(images)

benign_images = load_images_from_folder('/content/drive/MyDrive/debinew/Benign')
malicious_images = load_images_from_folder('/content/drive/MyDrive/debinew/Malicious')

benign_labels = np.zeros(len(benign_images))
malicious_labels = np.ones(len(malicious_images))

# Load CIFAR-10 dataset
(x_train_cifar, _), (x_test_cifar, _) = cifar10.load_data()
cifar_images = np.concatenate([x_train_cifar, x_test_cifar], axis=0)
cifar_images = np.array([tf.image.resize(img, (28, 28)).numpy() for img in cifar_images])
cifar_images = tf.image.rgb_to_grayscale(cifar_images).numpy()

cifar_labels = np.full(len(cifar_images), 2)

# Combine datasets
images = np.concatenate((benign_images, malicious_images, cifar_images), axis=0)
labels = np.concatenate((benign_labels, malicious_labels, cifar_labels), axis=0)

images = images.astype('float32') / 255

# Train VAE
vae = VAE(encoder, decoder)
vae.compile(optimizer=tf.keras.optimizers.Adam())
vae.fit(images, epochs=10, batch_size=128)

# 3D Plotting function with plotly
def plot_latent_space_3d(encoder, data, labels):
    z_mean, _, _ = encoder.predict(data)
    fig = px.scatter_3d(
        x=z_mean[:, 0],
        y=z_mean[:, 1],
        z=z_mean[:, 2],
        color=labels,
        labels={'x': 'z[0]', 'y': 'z[1]', 'z': 'z[2]', 'color': 'Class'},
        title="3D Latent Space"
    )
    fig.show()

# Plot the 3D latent space
plot_latent_space_3d(encoder, images, labels)


Model: "encoder"
__________________________________________________________________________________________________
 Layer (type)                Output Shape                 Param #   Connected to                  
 input_3 (InputLayer)        [(None, 28, 28, 1)]          0         []                            
                                                                                                  
 conv2d_2 (Conv2D)           (None, 14, 14, 64)           640       ['input_3[0][0]']             
                                                                                                  
 conv2d_3 (Conv2D)           (None, 7, 7, 128)            73856     ['conv2d_2[0][0]']            
                                                                                                  
 flatten_1 (Flatten)         (None, 6272)                 0         ['conv2d_3[0][0]']            
                                                                                            